In [1]:
# import plotly.plotly as py
from plotly.graph_objs import *
import pandas as pd
import numpy as np
import scipy as sp
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from nltk.tokenize import TweetTokenizer
from nltk.corpus import wordnet as wn
import plotly.tools as tls
import cufflinks as cf
import scipy.stats as stats
from plotly import __version__
import plotly.offline as py
from collections import Counter
import os
import datetime
from sklearn.cluster import KMeans
from sklearn.preprocessing import normalize, Normalizer
from sklearn.manifold import TSNE
import finsymbols

In [2]:
py.init_notebook_mode(connected=True)
cf.go_offline()


# Let's apply Concepts to Tweets
1. remove stopwords
2. lemmatize tweets
3. lowercase
3. count the length

In [4]:
# print stopwords.words('english')
lemmatizer = WordNetLemmatizer()
print lemmatizer.lemmatize('I').lower()

i


In [5]:
stops = set(stopwords.words('english')+['.',',','!','?',';',':','[',']','\"'])
def lemmatize_tweets(t):
    tokenizer = TweetTokenizer(preserve_case=False, reduce_len=True)
    tokens = tokenizer.tokenize(t)
    result = []
    for w in tokens:
        lemma = lemmatizer.lemmatize(w)
        if lemma not in stops:
            result.append(lemma)
    return result

# from IPython.core.debugger import Tracer; Tracer()()
            
test = 'Hello, I am a boy.'
print lemmatize_tweets(test)

[u'hello', u'boy']


In [7]:
def count_concept(tweets, concept_words, k):
    counter = Counter()
    count = 0
    for w in tweets:
        if w in concept_words:
            count += 1
            counter[w] += 1
    most_common = counter.most_common()
    
    top_k = most_common[:k-1]
    top_k.append(('etc',sum(d[1] for d in most_common[k-1:])))
    while len(top_k) < k:
        top_k.append(('n/a',0))
    return count, len(tweets) - count, top_k, counter

def odd_ratio(concept_words):
    hillary_count, hillary_not_count, hillary_counter, c = count_concept(lemma_tweets['HillaryClinton'], concept_words)
    trump_count, trump_not_count, trump_counter, c = count_concept(lemma_tweets['realDonaldTrump'], concept_words)
    
    odd_ratio = (trump_count*1.0/hillary_count)/(trump_not_count*1.0/hillary_not_count)
    if odd_ratio >= 0 :
        return odd_ratio, trump_counter
    else:
        return -1/odd_ratio, hillary_counter

def odd_ratio2(concept_words):
    hillary_count, hillary_not_count, hillary_counter, c  = count_concept(lemma_tweets['HillaryClinton'], concept_words,5)
    trump_count, trump_not_count, trump_counter, c = count_concept(lemma_tweets['realDonaldTrump'], concept_words,5)
    
    odd_ratio, pvalue = stats.fisher_exact([[trump_count, trump_not_count], [hillary_count, hillary_not_count]])
    if odd_ratio >= 1 :
        return odd_ratio, pvalue, trump_counter
    else:
        return -1/odd_ratio, pvalue, hillary_counter 

# NASDAQ 100 

1. 각각의 회사들의 twitter를 합쳐서
2. conceptvector로 만들어서 
3. clustering 할 것이다. 

In [8]:
nasdaq_files = os.listdir('./data/nasdaq/')
nasdaq_names = [n.split('_')[2] for n in nasdaq_files]

nasdaq = {}
for fname, stockname in zip(nasdaq_files, nasdaq_names):
    df = pd.read_excel('./data/nasdaq/%s' %fname, sheetname='Stream')
    df = df[df['Is a RT'] == False]
    df['time'] = pd.to_datetime(df['Date']+ ' ' + df['Hour'])
    df.set_index('time')
    nasdaq[stockname] = df

# Let's build Empath Concepts as dictionary

In [39]:
def remove_word(words, concepts):
    new_concepts = {}
    for c in concepts:
        new_concepts[c] = {w:True for w in concepts[c] if w not in words}
    return new_concepts

concepts = {}
with open('./data/categories.tsv','r') as f:
    for l in f:
        cols = l.strip().split('\t')
        name = cols[0]
        terms = cols[1:]
        concepts[name] = {c:True for c in terms}

nasdaq_symbols = finsymbols.get_nasdaq_symbols()
nasdaq_symbols_dict = {w['symbol'].lower():w['company'] for w in nasdaq_symbols}

nasdaq_symbols_dict['lmca'] = 'Liberty Media Formula One'
nasdaq_symbols_dict['lltc'] = 'Linear Technology Corporation'
nasdaq_symbols_dict['sndk'] = 'SanDisk Corporation'
nasdaq_symbols_dict['inct'] = 'InCapta Inc'
nasdaq_symbols_dict['lmck'] = 'Liberty Media Formula One'
# for name in company_names:
#     print nasdaq_symbols_dict[name]

nasdaq_full_name = [' '.join(nasdaq_symbols_dict[name].split('.')) for name in company_names]
# print nasdaq_full_name
nasdaq_name_bag = ' '.join(nasdaq_full_name)

nasdaq_lemma_names = lemmatize_tweets(nasdaq_name_bag)
print nasdaq_lemma_names
concepts_nasdaq = remove_word(['fox', 'trip', 'communication', 'discovvery', 'cost', 
                               'dish', 'technology', 'apple', 'cook', 'food','tree','bath', 
                               'boot', 'system', 'read', 'data', 'store',
                              'system','read','data','store','supply','company','product',
                              'analyst','discovery','research', 'pharmaceutical', 'western',
                              'international','airline','network','software',
                              'blizzard','dollar','instrument',
                              'facebook','google','twitter','corporation','advisor','global','tractor','bed',
                              'digital','cruise', 'surgical','beverage','monster','processing','interactive'], concepts)

concepts_nasdaq = remove_word(nasdaq_lemma_names, concepts_nasdaq)
concepts = concepts_nasdaq
        
nasdaq_tweets = {}
for stock in nasdaq:
    nasdaq_tweets[stock] = ' '.join(nasdaq[stock]['Tweet content'])

[u'american', u'airline', u'group', u'inc', u'apple', u'inc', u'adobe', u'system', u'incorporated', u'automatic', u'data', u'processing', u'inc', u'autodesk', u'inc', u'akamai', u'technology', u'inc', u'alexion', u'pharmaceutical', u'inc', u'applied', u'material', u'inc', u'amgen', u'inc', u'amazon', u'com', u'inc', u'activision', u'blizzard', u'inc', u'broadcom', u'limited', u'bed', u'bath', u'&', u'beyond', u'inc', u'baidu', u'inc', u'biomarin', u'pharmaceutical', u'inc', u'ca', u'inc', u'celgene', u'corporation', u'cerner', u'corporation', u'check', u'point', u'software', u'technology', u'ltd', u'charter', u'communication', u'inc', u'comcast', u'corporation', u'costco', u'wholesale', u'corporation', u'cisco', u'system', u'inc', u'csx', u'corporation', u'ctrip', u'com', u'international', u'ltd', u'cognizant', u'technology', u'solution', u'corporation', u'discovery', u'communication', u'inc', u'discovery', u'communication', u'inc', u'dish', u'network', u'corporation', u'dollar', u'tre

In [40]:
nasdaq_lemma_tweets = {}
for h in nasdaq_tweets:
    nasdaq_lemma_tweets[h] = lemmatize_tweets(nasdaq_tweets[h])

In [41]:
topk = 5
nasdaq_vectors = {}
nasdaq_topk_words = {}
nasdaq_counter = {}
nasdaq_count = {}
nasdaq_dict = {}
for company in nasdaq_tweets:
    nasdaq_vectors[company] = []
    nasdaq_topk_words[company] = {}
    nasdaq_counter[company] = {}
    nasdaq_count[company] = {}
    nasdaq_dict[company] = {}
    for c in concepts:
        count, not_count, topk_words, counter = count_concept(nasdaq_lemma_tweets[company], concepts[c], topk)
        nasdaq_vectors[company].append(count*1.0/(count+not_count))
        nasdaq_topk_words[company][c] = topk_words
        nasdaq_counter[company][c] = counter
        nasdaq_count[company][c] = [count, not_count]
        nasdaq_dict[company][c] = count*1.0/(count+not_count)

In [42]:
df = pd.DataFrame.from_dict(nasdaq_dict, orient='index')
df.head()

help    office     dance     money   wedding  valuable  \
aal   0.001139  0.002394  0.001894  0.017163  0.000883  0.011438   
aapl  0.002303  0.002292  0.001914  0.017610  0.001617  0.013126   
adbe  0.001465  0.003027  0.000952  0.013499  0.000513  0.011302   
adp   0.003902  0.002092  0.000905  0.018322  0.000679  0.011875   
adsk  0.001517  0.003034  0.001284  0.015229  0.000583  0.014179   

      domestic_work     sleep  medical_emergency      cold    ...     \
aal        0.000426  0.000521           0.000340  0.000606    ...      
aapl       0.001199  0.000945           0.000651  0.000855    ...      
adbe       0.000415  0.000586           0.000293  0.000220    ...      
adp        0.001640  0.000057           0.000452  0.000170    ...      
adsk       0.000175  0.000117           0.000175  0.000117    ...      

      feminine    weapon  children     ocean    giving  contentment   writing  \
aal   0.000138  0.001139  0.000362  0.000458  0.006065     0.000192  0.001043   
aapl  0.000450  0.001258  0.001085  0.000847  0.005528     0.000348  0.002165   
adbe  0.000269  0.002075  0.000342  0.000879  0.003002     0.000098  0.003051   
adp   0.000283  0.005655  0.000339  0.000565  0.004185     0.000113  0.001979   
adsk  0.000175  0.001225  0.000408  0.000934  0.001809     0.000058  0.002392   

         rural  positive_emotion   musical  
aal   0.000447          0.001649  0.001841  
aapl  0.000642          0.003764  0.003141  
adbe  0.000342          0.002197  0.001465  
adp   0.000452          0.002488  0.001018  
adsk  0.000117          0.002159  0.001926  

[5 rows x 194 columns]

In [43]:
# company_names = []
# company_vectors = []
# for company in nasdaq_vectors:
#     company_names.append(company)
#     company_vectors.append(nasdaq_vectors[company])
company_names = df.index.values
company_vectors = df.values

print company_vector.shape

(103, 194)


In [44]:
n_cluster = 10
kmeans = KMeans(n_clusters=n_cluster).fit(company_vectors)
cls_idx = kmeans.labels_
print cls_idx

[2 0 2 8 8 9 2 2 2 0 0 3 3 0 2 9 2 9 0 0 0 3 0 3 2 8 9 8 0 9 0 3 2 3 9 3 0
 3 2 2 2 0 0 9 9 7 2 3 9 2 2 6 6 9 9 2 9 4 0 2 2 9 0 2 8 9 2 0 9 2 0 2 3 8
 9 0 3 2 1 2 8 3 3 3 8 2 8 5 0 0 8 0 2 9 0 3 1 9 3 2 2 3 0]


In [60]:
df['cluster'] = pd.Series(cls_idx, index=company_names)
df.head()

help    office     dance     money   wedding  valuable  \
aal   0.001139  0.002394  0.001894  0.017163  0.000883  0.011438   
aapl  0.002303  0.002292  0.001914  0.017610  0.001617  0.013126   
adbe  0.001465  0.003027  0.000952  0.013499  0.000513  0.011302   
adp   0.003902  0.002092  0.000905  0.018322  0.000679  0.011875   
adsk  0.001517  0.003034  0.001284  0.015229  0.000583  0.014179   

      domestic_work     sleep  medical_emergency      cold   ...       weapon  \
aal        0.000426  0.000521           0.000340  0.000606   ...     0.001139   
aapl       0.001199  0.000945           0.000651  0.000855   ...     0.001258   
adbe       0.000415  0.000586           0.000293  0.000220   ...     0.002075   
adp        0.001640  0.000057           0.000452  0.000170   ...     0.005655   
adsk       0.000175  0.000117           0.000175  0.000117   ...     0.001225   

      children     ocean    giving  contentment   writing     rural  \
aal   0.000362  0.000458  0.006065     0.000192  0.001043  0.000447   
aapl  0.001085  0.000847  0.005528     0.000348  0.002165  0.000642   
adbe  0.000342  0.000879  0.003002     0.000098  0.003051  0.000342   
adp   0.000339  0.000565  0.004185     0.000113  0.001979  0.000452   
adsk  0.000408  0.000934  0.001809     0.000058  0.002392  0.000117   

      positive_emotion   musical  cluster  
aal           0.001649  0.001841        2  
aapl          0.003764  0.003141        0  
adbe          0.002197  0.001465        2  
adp           0.002488  0.001018        8  
adsk          0.002159  0.001926        8  

[5 rows x 195 columns]

In [73]:
print df.mean()[:5]

df_cluster = df.groupby('cluster').mean() 
df_cluster.head()

help       0.001873
office     0.002281
dance      0.001650
money      0.017324
wedding    0.000882
dtype: float64


help    office     dance     money   wedding  valuable  \
cluster                                                               
0        0.001899  0.002578  0.001574  0.015006  0.001365  0.010234   
1        0.001417  0.006697  0.000574  0.018571  0.000224  0.020579   
2        0.001645  0.002022  0.001862  0.015847  0.000688  0.010081   
3        0.002119  0.001732  0.001217  0.022754  0.001167  0.012511   
4        0.001281  0.003111  0.002562  0.017204  0.000732  0.012628   

         domestic_work     sleep  medical_emergency      cold    ...     \
cluster                                                          ...      
0             0.000954  0.001157           0.000495  0.000382    ...      
1             0.000412  0.000242           0.000323  0.000718    ...      
2             0.000506  0.000522           0.000749  0.000260    ...      
3             0.000545  0.000656           0.000399  0.000370    ...      
4             0.000366  0.000183           0.000000  0.000549    ...      

         feminine    weapon  children     ocean    giving  contentment  \
cluster                                                                  
0        0.000333  0.001343  0.000769  0.000733  0.003989     0.000236   
1        0.000000  0.003577  0.000179  0.000555  0.001920     0.000063   
2        0.000297  0.001593  0.000774  0.000778  0.002881     0.000159   
3        0.000196  0.002141  0.000413  0.000527  0.003928     0.000166   
4        0.000183  0.001830  0.000915  0.000549  0.001830     0.000366   

          writing     rural  positive_emotion   musical  
cluster                                                  
0        0.002179  0.000738          0.002595  0.002783  
1        0.000941  0.000224          0.000753  0.000574  
2        0.001939  0.000267          0.001789  0.002328  
3        0.001570  0.000758          0.002036  0.001813  
4        0.002562  0.000549          0.002379  0.002562  

[5 rows x 194 columns]

In [74]:
df_cluster = (df_cluster - df.mean())
df_cluster.drop('cluster', axis=1, inplace=True)
df_cluster.head()

achievement  affection  aggression  air_travel   alcohol   ancient  \
cluster                                                                       
0           0.000515   0.000064    0.000426    0.000715  0.000021  0.000027   
1          -0.001670  -0.000312   -0.000376   -0.000719 -0.000199 -0.000332   
2          -0.000123  -0.000023   -0.000110   -0.000236 -0.000002  0.000013   
3          -0.000166   0.000013   -0.000072   -0.000232  0.000061  0.000559   
4           0.000681  -0.000183    0.000016   -0.000707 -0.000199 -0.000203   

            anger    animal     anonymity  anticipation    ...      wealthy  \
cluster                                                    ...                
0        0.000096  0.000334  1.801592e-05      0.000031    ...    -0.001233   
1       -0.000167 -0.000576 -3.279960e-05     -0.000155    ...     0.000436   
2        0.000036 -0.000016  6.068714e-07      0.000014    ...    -0.000885   
3       -0.000055 -0.000126 -1.934547e-05      0.000007    ...     0.001923   
4        0.000382 -0.000077 -3.279960e-05     -0.000218    ...     0.000592   

           weapon   weather   wedding  white_collar_job      work   worship  \
cluster                                                                       
0       -0.000541  0.000130  0.000483         -0.000089  0.000811  0.000058   
1        0.001693  0.000140 -0.000657          0.004866  0.000894 -0.000121   
2       -0.000292 -0.000016 -0.000193         -0.000319 -0.000534 -0.000012   
3        0.000257  0.000151  0.000285         -0.000325 -0.000333 -0.000038   
4       -0.000054 -0.000516 -0.000150         -0.000474  0.000547  0.000977   

          writing     youth      zest  
cluster                                
0        0.000321  0.000156  0.000012  
1       -0.000917 -0.000288 -0.000072  
2        0.000081  0.000075 -0.000091  
3       -0.000288 -0.000059  0.000117  
4        0.000705 -0.000288 -0.000221  

[5 rows x 194 columns]

In [75]:
from sklearn.decomposition import PCA
pca = PCA(n_components=2)
company_pca = pca.fit_transform(company_vectors)


In [94]:
trace0 = Scatter(
  x=[d[0] for d in company_pca],
  y=[d[1] for d in company_pca],
  text=company_names,
  mode = 'markers',
  marker=dict(
      size=8,
      color=cls_idx,
      colorscale='Jet',
      colorbar=ColorBar(),
      opacity=0.8
  )
)
layout = Layout( title='Cluster %s' %title, autosize=False,
                        barmode='stack',
                       width=500,
                height=500,
               xaxis=dict(
        autorange=True,
        showgrid=False,
        zeroline=False,
        showline=False,
        autotick=True,
        ticks='',
        showticklabels=False
    ),
    yaxis=dict(
        autorange=True,
        showgrid=False,
        zeroline=False,
        showline=False,
        autotick=True,
        ticks='',
        showticklabels=False
    ))

data = [trace0]
fig = Figure(data=data, layout=layout)
py.iplot(fig)

In [77]:
data = [Heatmap(z=company_vectors)]
py.iplot(data)
# company_vectors

In [78]:
data = [Heatmap(z=df_cluster.values)]
py.iplot(data)

In [85]:
cluster_counter = [{} for i in range(n_cluster)]
cluster_count = [{} for i in range(n_cluster)]
for i, cluster in enumerate(cls_idx):
    for c  in concepts:
        if c in cluster_counter[cluster]:
            cluster_counter[cluster][c] += nasdaq_counter[company_names[i]][c]
            cluster_count[cluster][c][0] += nasdaq_count[company_names[i]][c][0]
            cluster_count[cluster][c][1] += nasdaq_count[company_names[i]][c][1]
        else:
            cluster_counter[cluster][c] = nasdaq_counter[company_names[i]][c]
            cluster_count[cluster][c] = nasdaq_count[company_names[i]][c]
            
def odd_ratio_cluster(cls_idx, concept, k):
    Bcounter, Bcount = Counter(), [0,0]
    for i in range(n_cluster):
        if i == cls_idx:
            Acounter = cluster_counter[i][concept]
            Acount =cluster_count[i][concept]
        else:
            Bcounter += cluster_counter[i][concept]
            Bcount[0] += cluster_count[i][concept][0]
            Bcount[1] += cluster_count[i][concept][1]
    
    odd_ratio = (Acount[0]*1.0/Acount[1])/(Bcount[0]*1.0/Bcount[1])
    most_common = Acounter.most_common()
    top_k_A = most_common[:k-1]
    top_k_A.append(('etc',sum(d[1] for d in most_common[k-1:])))
    while len(top_k_A) < k:
        top_k_A.append(('n/a',0))
        
    most_common = Bcounter.most_common()
    top_k_B = most_common[:k-1]
    top_k_B.append(('etc',sum(d[1] for d in most_common[k-1:])))
    while len(top_k_B) < k:
        top_k_B.append(('n/a',0))
    
    if odd_ratio > 1:
        return odd_ratio, Acount, top_k_A
    elif odd_ratio == 0:
        return -100, Acount, top_k_B
    else:
        return -1/odd_ratio, Bcount, top_k_B
pvalue=1
all_cluster_odds_ratio = []
for i in range(n_cluster):
    cluster_odds_ratio = []
    for c in concepts:
        odd_ratio, count, most_common = odd_ratio_cluster(i,c, 5)
#         print count
        if count[0] + count[1] == 0:
            from IPython.core.debugger import Tracer; debug_here = Tracer()
        if count[0]*1.0/(count[0]+count[1]) > 0.0001 and odd_ratio>2: 
            cluster_odds_ratio.append( (c, odd_ratio, pvalue, most_common ))
    cluster_odds_ratio.sort(key=lambda x: x[1], reverse=False)
    all_cluster_odds_ratio.append(cluster_odds_ratio)

In [87]:
for c_idx, cluster_odds_ratio in enumerate(all_cluster_odds_ratio):
    if len(cluster_odds_ratio) > 0:
        concepts_names = [d[0] for d in cluster_odds_ratio]
        topk = 5
        data = []
        for i in range(topk):
            trace = Bar( x=[d[3][i][1]*d[1]/sum(c[1] for c in d[3]) for d in cluster_odds_ratio],
                       y=[d[0] for d in cluster_odds_ratio],
                       text=[d[3][i][0] for d in cluster_odds_ratio],
                       orientation='h')
            data.append(trace)
        title = str(c_idx)  +'<br>' + '  '.join([nasdaq_symbols_dict[company_names[i]] if company_names[i] in nasdaq_symbols_dict else company_names[i] for i,c in enumerate(cls_idx) if c==c_idx])
        layout = Layout( title='Cluster %s' %title, autosize=True,
                        barmode='stack',
                       width=800,
                       height=1200)
        fig = Figure(data=data, layout=layout)
        py.iplot(fig)

In [84]:
for c_idx, cluster_odds_ratio in enumerate(all_cluster_odds_ratio):
    print 'Cluster %d' %c_idx
    print  ' \n'.join([nasdaq_symbols_dict[company_names[i]] if company_names[i] in nasdaq_symbols_dict else company_names[i] for i,c in enumerate(cls_idx) if c==c_idx])
    print  '--------'

Cluster 0
Apple Inc. 
Amazon.com, Inc. 
Activision Blizzard, Inc 
Baidu, Inc. 
Check Point Software Technologies Ltd. 
Charter Communications, Inc. 
Comcast Corporation 
Cisco Systems, Inc. 
DISH Network Corporation 
Electronic Arts Inc. 
Facebook, Inc. 
Alphabet Inc. 
Alphabet Inc. 
Marriott International 
Microsoft Corporation 
Netflix, Inc. 
NVIDIA Corporation 
The Priceline Group Inc.  
T-Mobile US, Inc. 
TripAdvisor, Inc. 
Tesla, Inc.  
Viacom Inc. 
Yahoo! Inc.
--------
Cluster 1
Liberty Interactive Corporation 
Verisk Analytics, Inc.
--------
Cluster 2
American Airlines Group, Inc. 
Adobe Systems Incorporated 
Alexion Pharmaceuticals, Inc. 
Applied Materials, Inc. 
Amgen Inc. 
BioMarin Pharmaceutical Inc. 
Celgene Corporation 
Ctrip.com International, Ltd. 
Endo International plc 
Twenty-First Century Fox, Inc. 
Twenty-First Century Fox, Inc. 
Gilead Sciences, Inc. 
Incyte Corporation 
JD.com, Inc. 
The Kraft Heinz Company 
Liberty Media Formula One 
Mattel, Inc. 
Mondelez Intern

# Findings

- 21st fox -> animal -> fox
- tripadvisor -> trip
- Communication company -> communications, discovery
    1. SBA Communications Corporation
    2. Discovery Communications, Inc. 
    1. Discovery Communications, Inc. 
    3. Charter Communications, Inc.
- Costco -> cost
- Dish Network -> Eating, Restaurant, cooking -> dish
- Technologies company -> technology
    1. Automatic Data Processing, Inc. 
    2. Check Point Software Technologies Ltd. 
    3. Akamai Technologies, Inc. 
    4. Linear Technology Corporation
    5. Cognizant Technology Solutions Corporation
- Lots of company -> Eating -> Apple, cook, dish

# Revision with updated Dictionary

In [136]:
concepts_nasdaq = remove_word(['fox', 'trip', 'communication', 'discovvery', 'cost', 
                               'dish', 'technology', 'apple', 'cook', 'food','tree','bath', 
                               'boot', 'system', 'read', 'data', 'store',
                              'system','read','data','store','supply','company','product',
                              'analyst','discovery','research', 'pharmaceutical', 'western',
                              'international','airline','network','software',
                              'blizzard','dollar','instrument',
                              'facebook','google','twitter','corporation','advisor','global','tractor','bed',
                              'digital','cruise', 'surgical','beverage','monster','processing','interactive'], concepts)

concepts_nasdaq = remove_word(nasdaq_lemma_names, concepts_nasdaq)
concepts = concepts_nasdaq

In [137]:

topk = 5
nasdaq_vectors = {}
nasdaq_topk_words = {}
nasdaq_counter = {}
nasdaq_count = {}
for company in nasdaq_tweets:
    nasdaq_vectors[company] = []
    nasdaq_topk_words[company] = {}
    nasdaq_counter[company] = {}
    nasdaq_count[company] = {}
    for c in concepts:
        count, not_count, topk_words, counter = count_concept(nasdaq_lemma_tweets[company], concepts[c], topk)
        nasdaq_vectors[company].append(count*1.0/(count+not_count))
        nasdaq_topk_words[company][c] = topk_words
        nasdaq_counter[company][c] = counter
        nasdaq_count[company][c] = [count, not_count]
        

In [138]:
company_names = []
company_vectors = []
for company in nasdaq_vectors:
    company_names.append(company)
    company_vectors.append(nasdaq_vectors[company])

In [139]:
n_cluster = 10
kmeans = KMeans(n_clusters=n_cluster).fit(company_vectors)
cls_idx = kmeans.labels_
print cls_idx

[3 8 3 4 3 3 4 0 3 4 8 0 3 0 5 0 8 5 0 1 3 8 8 3 3 8 3 0 0 9 2 0 0 8 0 3 3
 0 0 3 0 4 0 0 8 0 0 3 8 8 3 3 0 0 0 8 0 1 0 0 3 4 0 0 0 3 0 0 0 0 0 8 3 0
 0 0 3 4 3 4 3 0 3 3 3 0 3 3 0 4 6 0 0 0 0 0 3 7 8 0 8 0 0]


In [140]:
from sklearn.decomposition import PCA
pca = PCA(n_components=2)
company_pca = pca.fit_transform(company_vectors)

In [141]:
trace0 = Scatter(
  x=[d[0] for d in company_pca],
  y=[d[1] for d in company_pca],
  text=company_names,
  mode = 'markers',
  marker=dict(
      size=10,
      color=cls_idx,
      colorscale='Jet',
      colorbar=ColorBar()
  )
)

data = [trace0]
py.iplot(data, filename = 'basic-line')

In [142]:
model = TSNE(n_components=2)
company_tsne = model.fit_transform(company_vectors)
trace0 = Scatter(
  x=[d[0] for d in company_tsne],
  y=[d[1] for d in company_tsne],
  text=company_names,
  mode = 'markers',
  marker=dict(
      size=10,
      color=cls_idx,
      colorscale='Jet',
      colorbar=ColorBar()
  )
)

data = [trace0]
py.iplot(data, filename = 'basic-line')


In [143]:
data = [Heatmap(z=company_vectors)]
py.iplot(data)
# company_vectors

In [144]:
cluster_counter = [{} for i in range(n_cluster)]
cluster_count = [{} for i in range(n_cluster)]
for i, cluster in enumerate(cls_idx):
    for c  in concepts:
        if c in cluster_counter[cluster]:
            cluster_counter[cluster][c] += nasdaq_counter[company_names[i]][c]
            cluster_count[cluster][c][0] += nasdaq_count[company_names[i]][c][0]
            cluster_count[cluster][c][1] += nasdaq_count[company_names[i]][c][1]
        else:
            cluster_counter[cluster][c] = nasdaq_counter[company_names[i]][c]
            cluster_count[cluster][c] = nasdaq_count[company_names[i]][c]

In [145]:
all_cluster_odds_ratio = []
for i in range(n_cluster):
    cluster_odds_ratio = []
    for c in concepts:
        odd_ratio, count, most_common = odd_ratio_cluster(i,c, 5)
        if count[0]*1.0/(count[0]+count[1]) > 0.001 and odd_ratio>2: 
            cluster_odds_ratio.append( (c, odd_ratio, pvalue, most_common ))
    cluster_odds_ratio.sort(key=lambda x: x[1], reverse=False)
    all_cluster_odds_ratio.append(cluster_odds_ratio)


In [146]:
for c_idx, cluster_odds_ratio in enumerate(all_cluster_odds_ratio):
    if len(cluster_odds_ratio) > 0:
        concepts_names = [d[0] for d in cluster_odds_ratio]
        topk = 5
        data = []
        for i in range(topk):
            trace = Bar( x=[d[3][i][1]*d[1]/sum(c[1] for c in d[3]) for d in cluster_odds_ratio],
                       y=[d[0] for d in cluster_odds_ratio],
                       text=[d[3][i][0] for d in cluster_odds_ratio],
                       orientation='h')
            data.append(trace)
        title = str(c_idx)  +'<br>' + '  '.join([nasdaq_symbols_dict[company_names[i]] if company_names[i] in nasdaq_symbols_dict else company_names[i] for i,c in enumerate(cls_idx) if c==c_idx])
        layout = Layout( title='Cluster %s' %title, autosize=True,
                        barmode='stack',
                       width=800)
        fig = Figure(data=data, layout=layout)
        py.iplot(fig)

In [147]:
for c_idx, cluster_odds_ratio in enumerate(all_cluster_odds_ratio):
    print 'Cluster %d' %c_idx
    print  ' \n'.join([str(i) + ' , ' + company_names[i] + ' , ' + nasdaq_symbols_dict[company_names[i]] if company_names[i] in nasdaq_symbols_dict else str(i) + ' , ' + company_names[i] for i,c in enumerate(cls_idx) if c==c_idx])
    print  '----------------------------'

Cluster 0
7 , hsic , Henry Schein, Inc. 
11 , amgn , Amgen Inc. 
13 , disca , Discovery Communications, Inc. 
15 , mnst , Monster Beverage Corporation 
18 , wba , Walgreens Boots Alliance, Inc. 
27 , mdlz , Mondelez International, Inc. 
28 , celg , Celgene Corporation 
31 , endp , Endo International plc 
32 , tsla , Tesla, Inc.  
34 , ilmn , Illumina, Inc. 
37 , pcar , PACCAR Inc. 
38 , wdc , Western Digital Corporation 
40 , cern , Cerner Corporation 
42 , lrcx , Lam Research Corporation 
43 , txn , Texas Instruments Incorporated 
45 , tmus , T-Mobile US, Inc. 
46 , ca , CA Inc. 
52 , alxn , Alexion Pharmaceuticals, Inc. 
53 , vrtx , Vertex Pharmaceuticals Incorporated 
54 , ntap , NetApp, Inc. 
56 , sbux , Starbucks Corporation 
58 , akam , Akamai Technologies, Inc. 
59 , lltc , Linear Technology Corporation 
62 , yhoo , Yahoo! Inc. 
63 , isrg , Intuitive Surgical, Inc. 
64 , nxpi , NXP Semiconductors N.V. 
66 , wfm , Whole Foods Market, Inc. 
67 , aal , American Airlines Group, Inc.

In [62]:
print [c for c in concepts][149]


anger


# Now remove outlier companies

In [149]:
company_names = []
company_vectors = []
outliers = []
outliers_name = ['vrsk','qvca','symc','lbtya','lbtyk','mar','swks','lvnta']
for i,company in enumerate(nasdaq_vectors):
    if i in outliers or company in outliers_name:
        print company, i
    else:
        company_names.append(company)
        company_vectors.append(nasdaq_vectors[company])

lbtya 14
lbtyk 17
vrsk 19
lvnta 29
symc 30
qvca 57
mar 90
swks 97


In [150]:
len(nasdaq_vectors)

103

In [151]:
n_cluster = 10
kmeans = KMeans(n_clusters=n_cluster).fit(company_vectors)
cls_idx = kmeans.labels_
print cls_idx

[5 2 3 0 5 3 0 2 1 0 3 5 3 2 2 8 2 1 0 2 1 3 0 5 2 5 5 3 0 2 5 5 2 5 4 2 2
 2 5 0 3 2 6 0 0 9 5 5 2 2 0 3 2 2 3 0 3 2 5 3 3 5 2 2 5 0 5 3 2 3 3 0 5 0
 3 5 7 3 5 5 3 1 3 0 3 5 2 5 5 3 0 2 0 1 5]


In [152]:
from sklearn.decomposition import PCA
pca = PCA(n_components=2)
company_pca = pca.fit_transform(company_vectors)

In [153]:
trace0 = Scatter(
  x=[d[0] for d in company_pca],
  y=[d[1] for d in company_pca],
  text=company_names,
  mode = 'markers',
  marker=dict(
      size=10,
      color=cls_idx,
      colorscale='Jet',
      colorbar=ColorBar()
  )
)

data = [trace0]
py.iplot(data, filename = 'basic-line')

In [154]:
model = TSNE(n_components=2)
company_tsne = model.fit_transform(company_vectors)
trace0 = Scatter(
  x=[d[0] for d in company_tsne],
  y=[d[1] for d in company_tsne],
  text=company_names,
  mode = 'markers',
  marker=dict(
      size=10,
      color=cls_idx,
      colorscale='Jet',
      colorbar=ColorBar()
  )
)

data = [trace0]
py.iplot(data, filename = 'basic-line')


In [155]:
data = [Heatmap(z=company_vectors)]
py.iplot(data)
# company_vectors

In [156]:
cluster_counter = [{} for i in range(n_cluster)]
cluster_count = [{} for i in range(n_cluster)]
for i, cluster in enumerate(cls_idx):
    for c  in concepts:
        if c in cluster_counter[cluster]:
            cluster_counter[cluster][c] += nasdaq_counter[company_names[i]][c]
            cluster_count[cluster][c][0] += nasdaq_count[company_names[i]][c][0]
            cluster_count[cluster][c][1] += nasdaq_count[company_names[i]][c][1]
        else:
            cluster_counter[cluster][c] = nasdaq_counter[company_names[i]][c]
            cluster_count[cluster][c] = nasdaq_count[company_names[i]][c]

In [157]:
all_cluster_odds_ratio = []
for i in range(n_cluster):
    cluster_odds_ratio = []
    for c in concepts:
        odd_ratio, count, most_common = odd_ratio_cluster(i,c, 5)
        if count[0] > 300 and odd_ratio>2: 
            cluster_odds_ratio.append( (c, odd_ratio, pvalue, most_common ))
    cluster_odds_ratio.sort(key=lambda x: x[1], reverse=False)
    all_cluster_odds_ratio.append(cluster_odds_ratio)


In [158]:
for c_idx, cluster_odds_ratio in enumerate(all_cluster_odds_ratio):
    if len(cluster_odds_ratio) > 0:
        concepts_names = [d[0] for d in cluster_odds_ratio]
        topk = 5
        data = []
        for i in range(topk):
            trace = Bar( x=[d[3][i][1]*d[1]/sum(c[1] for c in d[3]) for d in cluster_odds_ratio],
                       y=[d[0] for d in cluster_odds_ratio],
                       text=[d[3][i][0] for d in cluster_odds_ratio],
                       orientation='h')
            data.append(trace)
        title = str(c_idx)  +'<br>' + '  '.join([nasdaq_symbols_dict[company_names[i]]  for i,c in enumerate(cls_idx) if c==c_idx])
        layout = Layout( title='Cluster %s' %title, autosize=True,
                        barmode='stack',
                       width=800)
        fig = Figure(data=data, layout=layout)
        py.iplot(fig)

In [159]:

for c_idx, cluster_odds_ratio in enumerate(all_cluster_odds_ratio):
    print 'Cluster %d' %c_idx
    print  ' \n'.join([str(i) + ' , ' + nasdaq_symbols_dict[company_names[i]] + ' , ' + company_names[i] for i,c in enumerate(cls_idx) if c==c_idx])
    print  '----------------------------'

Cluster 0
3 , Automatic Data Processing, Inc. , adp 
6 , Ross Stores, Inc. , rost 
9 , Tractor Supply Company , tsco 
18 , Costco Wholesale Corporation , cost 
22 , Broadcom Limited , avgo 
28 , O&#39;Reilly Automotive, Inc. , orly 
39 , Paychex, Inc. , payx 
43 , Express Scripts Holding Company , esrx 
44 , Intuit Inc. , intu 
50 , Fastenal Company , fast 
55 , Stericycle, Inc. , srcl 
65 , Bed Bath & Beyond Inc. , bbby 
71 , Maxim Integrated Products, Inc. , mxim 
73 , Autodesk, Inc. , adsk 
83 , Cognizant Technology Solutions Corporation , ctsh 
90 , Xilinx, Inc. , xlnx 
92 , SanDisk Corporation , sndk
----------------------------
Cluster 1
8 , Alphabet Inc. , goog 
17 , Electronic Arts Inc. , ea 
20 , NVIDIA Corporation , nvda 
81 , TripAdvisor, Inc. , trip 
93 , Activision Blizzard, Inc , atvi
----------------------------
Cluster 2
1 , SBA Communications Corporation , sbac 
7 , Henry Schein, Inc. , hsic 
13 , Discovery Communications, Inc. , disca 
14 , Monster Beverage Corporatio